In [1]:
import pandas as pd
import numpy as np

import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots

from scipy import stats
from statsmodels.stats.outliers_influence import variance_inflation_factor 

from sklearn.preprocessing import QuantileTransformer, LabelEncoder
from sklearn.model_selection import train_test_split

# Algorithms
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB

# Metrics
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score

import warnings
warnings.simplefilter(action = "ignore", category = Warning)

In [2]:
# Import dataset
crop = pd.read_csv("crop_recommendation.csv")

# Dataset overview
crop.shape # 8 variables and 2200 cases
crop.info() # 7 numeric variables and 1 object which should be categorical
crop["Crop"] = crop["Crop"].astype("category") # "Crop" as categorical

# Check null values
crop.isnull().sum()

# Check duplicates
crop.duplicated().sum()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2200 entries, 0 to 2199
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   Nitrogen     2200 non-null   int64  
 1   Phosphorus   2200 non-null   int64  
 2   Potassium    2200 non-null   int64  
 3   Temperature  2200 non-null   float64
 4   Humidity     2200 non-null   float64
 5   pH_Value     2200 non-null   float64
 6   Rainfall     2200 non-null   float64
 7   Crop         2200 non-null   object 
dtypes: float64(4), int64(3), object(1)
memory usage: 137.6+ KB


0

In [3]:
# Statistics
crop.describe().transpose()

count        mean        std        min        25%        50%  \
Nitrogen     2200.0   50.551818  36.917334   0.000000  21.000000  37.000000   
Phosphorus   2200.0   53.362727  32.985883   5.000000  28.000000  51.000000   
Potassium    2200.0   48.149091  50.647931   5.000000  20.000000  32.000000   
Temperature  2200.0   25.616244   5.063749   8.825675  22.769375  25.598693   
Humidity     2200.0   71.481779  22.263812  14.258040  60.261953  80.473146   
pH_Value     2200.0    6.469480   0.773938   3.504752   5.971693   6.425045   
Rainfall     2200.0  103.463655  54.958389  20.211267  64.551686  94.867624   

                    75%         max  
Nitrogen      84.250000  140.000000  
Phosphorus    68.000000  145.000000  
Potassium     49.000000  205.000000  
Temperature   28.561654   43.675493  
Humidity      89.948771   99.981876  
pH_Value       6.923643    9.935091  
Rainfall     124.267508  298.560117

In [4]:
# Categorical data
crop_count = pd.DataFrame({"Crop": crop.groupby("Crop").size().index,
                           "Count": crop.groupby("Crop").size().values})

fig = px.bar(crop_count, x = "Crop", y = "Count",
             color = "Crop", orientation = "v", 
             title = "Amount of each crop")
fig.update_layout(xaxis_title = "Crop", yaxis_title = "Count", showlegend = False)
fig.show()

In [5]:
# Numerical data
# Histograms
fig = make_subplots(rows = 4, cols = 2, 
                    subplot_titles = crop.columns.to_list()[:7])
nitrogen = go.Histogram(x = crop.iloc[:,0])
phosphorus = go.Histogram(x = crop.iloc[:,1])
potassium = go.Histogram(x = crop.iloc[:,2])
temperature = go.Histogram(x = crop.iloc[:,3])
humidity = go.Histogram(x = crop.iloc[:,4])
ph = go.Histogram(x = crop.iloc[:,5])
rainfall = go.Histogram(x = crop.iloc[:,6])

fig.append_trace(nitrogen, 1, 1)
fig.append_trace(phosphorus, 1, 2)
fig.append_trace(potassium, 2, 1)
fig.append_trace(temperature, 2, 2)
fig.append_trace(humidity, 3, 1)
fig.append_trace(ph, 3, 2)
fig.append_trace(rainfall, 4, 1)

fig.update_layout(title_text= "Histograms of Numeric Data",
                  showlegend=False, autosize = False, width = 750, height = 750)
fig.update_annotations(font_size=11)
fig.update_xaxes(minor=dict(ticklen = 3, tickcolor = "black", showgrid = False))
fig.update_yaxes(minor_ticks = "inside")
fig.show()

# Boxplots
fig = make_subplots(rows = 4, cols = 2, 
                    subplot_titles = crop.columns.to_list()[:7])
nitrogen = go.Box(x = crop.iloc[:,0], name = "")
phosphorus = go.Box(x = crop.iloc[:,1], name = "")
potassium = go.Box(x = crop.iloc[:,2], name = "")
temperature = go.Box(x = crop.iloc[:,3], name = "")
humidity = go.Box(x = crop.iloc[:,4], name = "")
ph = go.Box(x = crop.iloc[:,5], name = "")
rainfall = go.Box(x = crop.iloc[:,6], name = "")

fig.append_trace(nitrogen, 1, 1)
fig.append_trace(phosphorus, 1, 2)
fig.append_trace(potassium, 2, 1)
fig.append_trace(temperature, 2, 2)
fig.append_trace(humidity, 3, 1)
fig.append_trace(ph, 3, 2)
fig.append_trace(rainfall, 4, 1)

fig.update_layout(title_text= "Boxplots of Numeric Data",
                  showlegend=False, autosize = False, width = 750, height = 750)
fig.update_annotations(font_size=11)
fig.update_xaxes(minor=dict(ticklen = 3, tickcolor = "black", showgrid = False))
fig.update_yaxes(minor_ticks = "inside")
fig.show()

In [6]:
# Bivariate analysis
print(crop.columns.to_list()[:7])

for elem in crop.columns.to_list()[0:7]:
    fig = px.box(crop, x = "Crop", y = elem, color = "Crop")
    fig.update_layout(showlegend = False)
    # fig.write_image("box_crop_"+elem+".png")
    fig.show()

['Nitrogen', 'Phosphorus', 'Potassium', 'Temperature', 'Humidity', 'pH_Value', 'Rainfall']


In [7]:
# Multivariate analysis
# Correlation
corr = crop.iloc[:,:7].corr().round(decimals = 4)
mask = np.triu(np.ones_like(corr, dtype = bool))
corr_mask = corr.mask(mask)

# Graph
fig = ff.create_annotated_heatmap(z=corr_mask.to_numpy(), 
                                  x=corr_mask.columns.tolist(),
                                  y=corr_mask.columns.tolist(),
                                  colorscale=px.colors.diverging.RdBu,
                                  hoverinfo="none", #Shows hoverinfo for null values
                                  showscale=True, ygap=1, xgap=1)

fig.update_xaxes(side="bottom")

fig.update_layout(
    title_text='Heatmap', 
    title_x=0.5, 
    width=750, 
    height=750,
    xaxis_showgrid=False,
    yaxis_showgrid=False,
    xaxis_zeroline=False,
    yaxis_zeroline=False,
    yaxis_autorange='reversed',
    template='plotly_white')

fig.show()

In [8]:
# Variance Inflation Factor
def compute_vif(considered_features):
    
    X = crop[considered_features]
    # the calculation of variance inflation requires a constant
    X['intercept'] = 1
    
    # create dataframe to store vif values
    vif = pd.DataFrame()
    vif["Variable"] = X.columns
    vif["VIF"] = [variance_inflation_factor(X.values, i) for i in range(X.shape[1])]
    vif = vif[vif['Variable']!='intercept']
    return vif

compute_vif(crop.columns.to_list()[:7])

Variable       VIF
0     Nitrogen  1.097026
1   Phosphorus  2.630465
2    Potassium  2.797118
3  Temperature  1.111104
4     Humidity  1.368986
5     pH_Value  1.055803
6     Rainfall  1.037426

In [9]:
# Outliers
# IQR = Q3-Q1
# Lower bound = Q1-1.5*IQR
# Upper bound = Q3+1.5*IQR

# Calculate Q1 and Q3
Q1 = crop.iloc[:,:7].quantile(0.25)
Q3 = crop.iloc[:,:7].quantile(0.75)

# Calculate IQR
IQR = Q3-Q1

# Lower and upper bounds
lower_bound = Q1-1.5*IQR
upper_bound = Q3+1.5*IQR

# Identify the outliers
outliers = (crop.iloc[:,:7] < lower_bound) | (crop.iloc[:,:7] > upper_bound)

# Remove outliers
crop_no_outliers = crop[~outliers.any(axis = 1)]
crop_no_outliers.reset_index(inplace = True, drop = True)

# Check count of each categorical data
crop_count = pd.DataFrame({"Crop": crop_no_outliers.groupby("Crop").size().index,
                           "Count": crop_no_outliers.groupby("Crop").size().values})

fig = px.bar(crop_count, x = "Crop", y = "Count",
             color = "Crop", orientation = "v", 
             title = "Amount of each crop after removing outliers")
fig.update_layout(xaxis_title = "Crop", yaxis_title = "Count", showlegend = False)
fig.show()

In [10]:
# Calculate skewness for each variable
# Histograms
titles = []
for column in crop.columns.to_list()[:7]:
    titles += [f"Original distribution of {column}. Skewness = {crop[column].skew().round(decimals = 4)}"]

fig = make_subplots(rows = 4, cols = 2, 
                    subplot_titles = titles)
nitrogen = go.Histogram(x = crop.iloc[:,0])
phosphorus = go.Histogram(x = crop.iloc[:,1])
potassium = go.Histogram(x = crop.iloc[:,2])
temperature = go.Histogram(x = crop.iloc[:,3])
humidity = go.Histogram(x = crop.iloc[:,4])
ph = go.Histogram(x = crop.iloc[:,5])
rainfall = go.Histogram(x = crop.iloc[:,6])

fig.append_trace(nitrogen, 1, 1)
fig.append_trace(phosphorus, 1, 2)
fig.append_trace(potassium, 2, 1)
fig.append_trace(temperature, 2, 2)
fig.append_trace(humidity, 3, 1)
fig.append_trace(ph, 3, 2)
fig.append_trace(rainfall, 4, 1)

fig.update_layout(title_text= "Skewness of Numeric Data",
                  showlegend=False, autosize = False, width = 750, height = 750)
fig.update_annotations(font_size=11)
fig.update_xaxes(minor=dict(ticklen = 3, tickcolor = "black", showgrid = False))
fig.update_yaxes(minor_ticks = "inside")
fig.show()

In [11]:
pd.DataFrame(QuantileTransformer(output_distribution = "normal", random_state = 0).fit_transform(crop["Nitrogen"].values.reshape((-1,1)))).values

array([[0.8074289 ],
       [0.68476299],
       [0.32822342],
       ...,
       [1.83122433],
       [1.73307081],
       [1.20753226]])

In [12]:
# Fix skewness with different transformations
print((crop.iloc[:,:7].values <= 0).any()) # True, so BoxCox cannot be used.

# Create copy dataframe
crop_copy = crop.copy(deep = True)

for column in crop.columns.to_list()[0:7]:
    # Fill in copy dataframe
    crop_copy["Original_"+column] = crop[column]
    crop_copy["Log_"+column] = np.log(crop[column])
    crop_copy["SQRT_"+column] = np.sqrt(crop[column])
    crop_copy["YeoJohnson_"+column], _ = stats.yeojohnson(crop[column])
    crop_copy["QuantileTransf_"+column] = QuantileTransformer(output_distribution = "normal", 
                                                              random_state = 0).fit_transform(crop[column].values.reshape((-1,1)))

    # Titles
    transformations = ["Original_", "Log_", "SQRT_", "YeoJohnson_", "QuantileTransf_"]
    titles = []
   
    for transf in transformations:
            titles += [f"{transf}{column}. Skewness = {crop_copy[transf+column].skew().round(decimals = 4)}"]

    # Figures
    fig = make_subplots(rows = 3, cols = 2, 
                subplot_titles = titles)
    
    trace1 = go.Histogram(x = crop_copy["Original_"+column])   
    trace2 = go.Histogram(x = crop_copy["Log_"+column])
    trace3 = go.Histogram(x = crop_copy["SQRT_"+column])
    trace4 = go.Histogram(x = crop_copy["YeoJohnson_"+column])
    trace5 = go.Histogram(x = crop_copy["QuantileTransf_"+column])

    fig.add_trace(trace1, 1, 1)
    fig.add_trace(trace2, 1, 2)
    fig.add_trace(trace3, 2, 1)
    fig.add_trace(trace4, 2, 2)
    fig.add_trace(trace5, 3, 1)

    fig.update_layout(title_text= f"Transformation to fix skewness of {column}",
        showlegend=False, autosize = False, width = 750, height = 750)
    fig.update_annotations(font_size=11)
    fig.update_xaxes(minor=dict(ticklen = 3, tickcolor = "black", showgrid = False))
    fig.update_yaxes(minor_ticks = "inside")
    fig.show()

True


In [13]:
# Transform the dataset
crop_std = crop.copy(deep = True)

for column in crop.columns.to_list()[:7]:
    # Create copy dataframe
    crop_std[column] = crop_copy["QuantileTransf_"+column]

print(crop_std.describe().transpose())

# Encode labels
print(crop_std.iloc[:,-1].unique()) # 22 labels
crop_std.iloc[:,-1] = LabelEncoder().fit_transform(crop_std.iloc[:,-1]) # Transform
print(crop_std.iloc[:,-1].unique()) # Check encoding

labels = pd.DataFrame({"Name": crop["Crop"].unique(), "Encoded": crop_std["Crop"].unique()}).sort_values(by = "Encoded", ascending = True)


# Get training and testing data
X_train, X_test, y_train, y_test = train_test_split(crop_std.iloc[:,0:6], 
                                                    crop_std.iloc[:,-1], 
                                                    test_size = 0.2, 
                                                    random_state = 123)

              count      mean       std       min       25%       50%  \
Nitrogen     2200.0 -0.029076  1.127859 -5.199338 -0.675277  0.001255   
Phosphorus   2200.0 -0.017168  1.125099 -5.199338 -0.675277 -0.002509   
Potassium    2200.0  0.012468  1.106659 -5.199338 -0.720087  0.003764   
Temperature  2200.0 -0.000065  1.008303 -5.199338 -0.674002  0.000074   
Humidity     2200.0  0.000262  1.009761 -5.199338 -0.674141 -0.000138   
pH_Value     2200.0  0.000162  1.010483 -5.199338 -0.674291  0.000129   
Rainfall     2200.0  0.000324  1.009625 -5.199338 -0.673998 -0.000160   

                  75%       max  
Nitrogen     0.668234  5.199338  
Phosphorus   0.673702  5.199338  
Potassium    0.689529  5.199338  
Temperature  0.674027  5.199338  
Humidity     0.674397  5.199338  
pH_Value     0.675034  5.199338  
Rainfall     0.674438  5.199338  
['Rice', 'Maize', 'ChickPea', 'KidneyBeans', 'PigeonPeas', ..., 'Papaya', 'Coconut', 'Cotton', 'Jute', 'Coffee']
Length: 22
Categories (22, obj

In [14]:
# SVC
# Models and hyperparameters
models = ["linear", "poly", "rbf", "sigmoid"]
c_values = [float(i) for i in [1, 10, 100, 1000]]

# Variables
len_mod = len(models)
len_c = len(c_values)

# Metrics
accuracies = np.zeros(shape = (len_mod, len_c))
predicts = np.zeros(shape = (len_mod*len_c, len(y_test)))

# Training and evaluation
for i, mod in enumerate(models):
    for j, c_value in enumerate(c_values):
        # Model
        model = SVC(kernel = mod, C = c_value)

        # Train
        model.fit(X_train, y_train)
        
        # Predict
        predict = model.predict(X_test)
        predicts[len_c*i+j,:] = predict
       
        # Metrics
        report = classification_report(y_test, predict, target_names = labels["Name"].values)
        accuracies[i,j] = accuracy_score(y_test, predict)

max_mod, max_c = np.unravel_index(np.argmax(accuracies, axis=None), accuracies.shape)

# Figure
fig = px.imshow(confusion_matrix(y_test, predicts[len_c*max_mod+max_c,:]), x = labels["Name"].values, 
                y = labels["Name"].values, color_continuous_scale = px.colors.qualitative.Plotly)
fig.update_yaxes(tickmode = "linear")
fig.update_xaxes(tickmode = "linear")
fig.update_layout(title_text = f"Heatmap of best kernel, being {models[max_mod]} SVM (C = {c_values[max_c]}) with an accuracy of {accuracies[max_mod, max_c]:<8.4f}")
fig.show()

print(f'The model with higher accuracy is: {models[max_mod]} SVM (C = {c_values[max_c]}) with an accuracy of {accuracies[max_mod, max_c]:<8.4f}.')

The model with higher accuracy is: rbf SVM (C = 100.0) with an accuracy of 0.9591  .


In [15]:
# Random Forest
# Hyperparameters
n_trees = [10, 100, 500, 1000]

# Metrics
accuracies = []
predicts = np.zeros(shape = len(y_test))

# Training and evaluation
for n_tree in n_trees:
    # Model
    model = RandomForestClassifier(n_estimators = n_tree)

    # Train
    model.fit(X_train, y_train)
    
    # Predict
    predict = model.predict(X_test)
    predicts = np.vstack((predicts, predict))

    # Metrics
    report = classification_report(y_test, predict, target_names = labels["Name"].values)
    accuracy = accuracy_score(y_test, predict)
    accuracies += [round(accuracy, 4)]

# Erase first row with zeros
predicts = np.delete(predicts, 0, 0)

# Figure
fig = px.imshow(confusion_matrix(y_test, predicts[np.argmax(accuracies)]), x = labels["Name"].values, 
                y = labels["Name"].values, color_continuous_scale = px.colors.qualitative.Plotly)
fig.update_yaxes(tickmode = "linear")
fig.update_xaxes(tickmode = "linear")
fig.update_layout(title_text = f"Heatmap of Random Forest best number of trees, being {n_trees[np.argmax(accuracies)]} with an accuracy of {accuracies[np.argmax(accuracies)]}")
fig.show()

print(f"The model with higher accuracy is: Random Forest with {n_trees[np.argmax(accuracies)]} number of trees and an accuracy of {accuracies[np.argmax(accuracies)]}.")

The model with higher accuracy is: Random Forest with 500 number of trees and an accuracy of 0.9795.


In [16]:
# Decision Tree
# Model
model = DecisionTreeClassifier()

# Train
model.fit(X_train, y_train)

# Predict
predict = model.predict(X_test)

# Metrics
report = classification_report(y_test, predict, target_names = labels["Name"].values)
accuracy = accuracy_score(y_test, predict)

# Figure
fig = px.imshow(confusion_matrix(y_test, predict), x = labels["Name"].values, 
                y = labels["Name"].values, color_continuous_scale = px.colors.qualitative.Plotly)
fig.update_yaxes(tickmode = "linear")
fig.update_xaxes(tickmode = "linear")
fig.update_layout(title_text = f"Heatmap of Decision Tree algorithm with an accuracy of {round(accuracy, 4)}")
fig.show()

print(f"The algorithm Decision Tree obtained an accuracy of {round(accuracy, 4)}.")


The algorithm Decision Tree obtained an accuracy of 0.9523.


In [17]:
# KNN
# Hyperparameters
k_neighbors = [1, 3, 5, 7]

# Metrics
accuracies = []
predicts = np.zeros(shape = len(y_test))

# Training and evaluation
for k_neighbor in k_neighbors:
    # Model
    model = KNeighborsClassifier(n_neighbors = k_neighbor)

    # Train
    model.fit(X_train, y_train)
    
    # Predict
    predict = model.predict(X_test)
    predicts = np.vstack((predicts, predict))

    # Metrics
    report = classification_report(y_test, predict, target_names = labels["Name"].values)
    accuracy = accuracy_score(y_test, predict)
    accuracies += [round(accuracy, 4)]

# Erase first row with zeros
predicts = np.delete(predicts, 0, 0)

# Figure
fig = px.imshow(confusion_matrix(y_test, predicts[np.argmax(accuracies)]), x = labels["Name"].values, 
                y = labels["Name"].values, color_continuous_scale = px.colors.qualitative.Plotly)
fig.update_yaxes(tickmode = "linear")
fig.update_xaxes(tickmode = "linear")
fig.update_layout(title_text = f"Heatmap of KNN algorithm (k = {k_neighbors[np.argmax(accuracies)]}) with an accuracy of {accuracies[np.argmax(accuracies)]}")
fig.show()

print(f"The model with higher accuracy is: KNN with k = {k_neighbors[np.argmax(accuracies)]} and an accuracy of {accuracies[np.argmax(accuracies)]}.")

The model with higher accuracy is: KNN with k = 5 and an accuracy of 0.9432.


In [18]:
# Naive Bayes
# Model
model = GaussianNB()

# Train
model.fit(X_train, y_train)

# Predict
predict = model.predict(X_test)

# Metrics
report = classification_report(y_test, predict, target_names = labels["Name"].values)
accuracy = accuracy_score(y_test, predict)

# Figure
fig = px.imshow(confusion_matrix(y_test, predict), x = labels["Name"].values, 
                y = labels["Name"].values, color_continuous_scale = px.colors.qualitative.Plotly)
fig.update_yaxes(tickmode = "linear")
fig.update_xaxes(tickmode = "linear")
fig.update_layout(title_text = f"Heatmap of Naive Bayes algorithm with an accuracy of {round(accuracy, 4)}")
fig.show()

print(f"The algorithm Naive Bayes obtained an accuracy of {round(accuracy, 4)}.")

The algorithm Naive Bayes obtained an accuracy of 0.9659.
